<a href="https://colab.research.google.com/github/WildAlex37/g_search_lite/blob/main/G_search_lite_cleaning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Récupération de la Data et cleaning


In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
import datetime as dt
import os
pd.options.display.max_columns = None

In [ ]:
import os
import json
import time
import requests
import pandas as pd
from datetime import datetime, timedelta

# IGDB API credentials
CLIENT_ID = "v4dlufpsiskkalr4ht57stnpxeh3lo"
CLIENT_SECRET = "8a1okhz512zn4lenv42jzt30c24gd9"

# IGDB API endpoints
AUTH_URL = 'https://id.twitch.tv/oauth2/token'
API_ENDPOINT = 'https://api.igdb.com/v4/games'

# Define the platform IDs for Xbox Series, PS5, and Switch
PLATFORM_IDS = {
    'Xbox Series': 169,  # Xbox Series X/S
    'PS5': 167,          # PlayStation 5
    'Switch': 130        # Nintendo Switch
}

def get_access_token():
    auth_params = {
        'client_id': CLIENT_ID,
        'client_secret': CLIENT_SECRET,
        'grant_type': 'client_credentials'
    }
    auth_response = requests.post(AUTH_URL, params=auth_params)
    return auth_response.json()['access_token']

def fetch_games(access_token, time_back: int=365, offset=0):
    headers = {
        'Client-ID': CLIENT_ID,
        'Authorization': f'Bearer {access_token}',
    }

    # Calculate the timestamp for a certain period
    limit_time = int((datetime.now() - timedelta(days=time_back)).timestamp())
    current_time = int(datetime.now().timestamp())

    # IGDB API query with rating, rating_count, and platform filter
    body = f"""
    fields name, first_release_date, release_dates.date, genres.name, platforms.name, summary, cover.url, rating, rating_count;
    where first_release_date >= {limit_time}
    & release_dates.date <= {current_time}
#    & platforms = ({PLATFORM_IDS['Xbox Series']}, {PLATFORM_IDS['PS5']}, {PLATFORM_IDS['Switch']});
    sort first_release_date desc;
    limit 500;
    offset {offset};
    """

    response = requests.post(API_ENDPOINT, headers=headers, data=body)
    return response.json()

def get_games(time_back: int):
    access_token = get_access_token()
    all_games = []
    offset = 0

    while True:
        games = fetch_games(access_token, time_back, offset)
        if not games:
            break

        all_games.extend(games)
        print(f"Fetched {len(games)} games. Total: {len(all_games)}")

        if len(games) < 500:
            break

        offset += 500
        time.sleep(0.3)  # Respect rate limits

    # Save all games to a JSON file
    with open('games_entry.json', 'w') as f:
        json.dump(all_games, f, indent=4)

    print(f"Scraped a total of {len(all_games)} games from the last {time_back} days.")
    return all_games

def flatten_data(games):
    flattened_games = []
    for game in games:
        flattened_game = {
            'name': game.get('name'),
            'first_release_date': pd.to_datetime(game.get('first_release_date'), unit='s') if game.get('first_release_date') else None,
            'genres': ', '.join([genre['name'] for genre in game.get('genres', [])]),
            'platforms': ', '.join([platform['name'] for platform in game.get('platforms', [])]),
            'summary': game.get('summary'),
            'rating': game.get('rating'),
            'rating_count': game.get('rating_count'),
            'cover': game.get('cover', {}).get('url') if isinstance(game.get('cover', {}), dict) else None
        }
        flattened_games.append(flattened_game)
    return flattened_games

if __name__ == "__main__":
    games = get_games(10000)
    flattened_games = flatten_data(games)

    # Create a DataFrame from the flattened data
    df = pd.DataFrame(flattened_games)

    # Filter the DataFrame for the relevant platforms
    df = df[df['platforms'].str.contains('PlayStation 5|Xbox Series|Nintendo Switch', na=False)]

    # Export to Parquet
    df.to_parquet('df_filtered.parquet')

    # Display the filtered DataFrame
    print(df.head())


Fetched 500 games. Total: 500
Fetched 500 games. Total: 1000
Fetched 500 games. Total: 1500
Fetched 500 games. Total: 2000
Fetched 500 games. Total: 2500
Fetched 500 games. Total: 3000
Fetched 500 games. Total: 3500
Fetched 500 games. Total: 4000
Fetched 500 games. Total: 4500
Fetched 500 games. Total: 5000
Fetched 500 games. Total: 5500
Fetched 500 games. Total: 6000
Fetched 500 games. Total: 6500
Fetched 500 games. Total: 7000
Fetched 500 games. Total: 7500
Fetched 500 games. Total: 8000
Fetched 500 games. Total: 8500
Fetched 500 games. Total: 9000
Fetched 500 games. Total: 9500
Fetched 500 games. Total: 10000
Fetched 500 games. Total: 10500
Fetched 500 games. Total: 11000
Fetched 500 games. Total: 11500
Fetched 500 games. Total: 12000
Fetched 500 games. Total: 12500
Fetched 500 games. Total: 13000
Fetched 500 games. Total: 13500
Fetched 500 games. Total: 14000
Fetched 500 games. Total: 14500
Fetched 500 games. Total: 15000
Fetched 500 games. Total: 15500
Fetched 500 games. Total: 16

In [ ]:
df.sample(5)

name first_release_date  \
14306                                     Rogue Explorer         2021-03-12   
7241                                     MLB The Show 23         2023-03-28   
15949                                       Package Inc.         2020-08-14   
22070                 Zaccaria Pinball: Aerobatics Table         2016-06-16   
792    That Time I Got Reincarnated as a Slime: Iseka...         2024-08-08   

                                                  genres  \
14306  Platform, Role-playing (RPG), Hack and slash/B...   
7241                                    Simulator, Sport   
15949                        Puzzle, Simulator, Strategy   
22070                                     Pinball, Indie   
792                                   Role-playing (RPG)   

                                               platforms  \
14306  PC (Microsoft Windows), PlayStation 4, Xbox On...   
7241   PlayStation 4, Xbox One, Nintendo Switch, Play...   
15949                               iOS, Nintendo Switch   
22070  Linux, PC (Microsoft Windows), Mac, Nintendo S...   
792           Xbox One, Nintendo Switch, Xbox Series X|S   

                                                 summary     rating  \
14306  Pixel Art Hack & Slash Roguelike Action! Do yo...        NaN   
7241                       Shock The Game. Own The Show.  85.978744   
15949  Package Inc. is an inspiring delivery simulato...        NaN   
22070  Aerobatics Table is a flying themed pinball ta...        NaN   
792    The Digital Deluxe Edition includes That Time ...        NaN   

       rating_count                                              cover  
14306           NaN  //images.igdb.com/igdb/image/upload/t_thumb/co...  
7241            6.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  
15949           NaN  //images.igdb.com/igdb/image/upload/t_thumb/co...  
22070           NaN  //images.igdb.com/igdb/image/upload/t_thumb/co...  
792             NaN  //images.igdb.com/igdb/image/upload/t_thumb/co...

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 23458 entries, 0 to 23457
Data columns (total 8 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   name                23458 non-null  object        
 1   first_release_date  23458 non-null  datetime64[ns]
 2   genres              23458 non-null  object        
 3   platforms           23458 non-null  object        
 4   summary             21395 non-null  object        
 5   rating              4685 non-null   float64       
 6   rating_count        4685 non-null   float64       
 7   cover               21357 non-null  object        
dtypes: datetime64[ns](1), float64(2), object(5)
memory usage: 1.4+ MB


## En TRAVAUX ##

In [ ]:
from google.colab import files
df.to_parquet('df_triple.parquet')
files.download('df_triple.parquet')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
df["first_release_date"] = pd.to_datetime(df["first_release_date"])

current_year = pd.Timestamp.now().year
df['year'] = df['first_release_date'].dt.year
df = df[df['year'] <= current_year]
df['decennie'] = (df['year'] // 10) * 10

<ipython-input-21-5ee3c7ef98e9>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["first_release_date"] = pd.to_datetime(df["first_release_date"])
<ipython-input-21-5ee3c7ef98e9>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['year'] = df['first_release_date'].dt.year


In [ ]:
df.head(10)

name first_release_date  \
2                                    Ground Zero Hero         2024-12-31   
3                                     Re:Pik 3 Deluxe         2024-12-25   
4                           Call of Duty: Black Ops 6         2024-10-25   
5                                            Damikira         2024-10-02   
6                                         Kill Knight         2024-10-02   
7                             Dave the Diver: Mxmtoon         2024-10-01   
8                             Dave the Diver: Balatro         2024-10-01   
9                        Dave the Diver: Potion Craft         2024-10-01   
10  Guilty Gear: Strive - Additional Character 14:...         2024-10-01   
11  Sword Art Online: Fractured Daydream - Premium...         2024-10-01   

                    genres                                          platforms  \
2         Adventure, Indie  PC (Microsoft Windows), Nintendo Switch, Xbox ...   
3      Strategy, Adventure                                    Nintendo Switch   
4                  Shooter  PC (Microsoft Windows), PlayStation 4, Xbox On...   
5          Shooter, Arcade                                    Nintendo Switch   
6   Shooter, Indie, Arcade  PC (Microsoft Windows), Nintendo Switch, PlayS...   
7                           PC (Microsoft Windows), Mac, PlayStation 4, Ni...   
8                           PC (Microsoft Windows), Mac, PlayStation 4, Ni...   
9                           PC (Microsoft Windows), Mac, PlayStation 4, Ni...   
10                          PC (Microsoft Windows), PlayStation 4, Xbox On...   
11                                                            Nintendo Switch   

                                              summary  rating  rating_count  \
2   Wacky action-roguelite survival in a post-apoc...     NaN           NaN   
3                                                None     NaN           NaN   
4   Developed by Treyarch and Raven, Black Ops 6 i...     NaN           NaN   
5   Use your grappling hook and blast your way thr...     NaN           NaN   
6   KILL KNIGHT is an ultra-responsive arcade-insp...     NaN           NaN   
7                                                None     NaN           NaN   
8                                                None     NaN           NaN   
9                                                None     NaN           NaN   
10  Adds Queen Dizzy to the roster of playable cha...     NaN           NaN   
11                                               None     NaN           NaN   

                                                cover  year  decennie  
2   //images.igdb.com/igdb/image/upload/t_thumb/co...  2024      2020  
3   //images.igdb.com/igdb/image/upload/t_thumb/co...  2024      2020  
4   //images.igdb.com/igdb/image/upload/t_thumb/co...  2024      2020  
5   //images.igdb.com/igdb/image/upload/t_thumb/co...  2024      2020  
6   //images.igdb.com/igdb/image/upload/t_thumb/co...  2024      2020  
7                                                None  2024      2020  
8                                                None  2024      2020  
9                                                None  2024      2020  
10                                               None  2024      2020  
11                                               None  2024      2020

In [ ]:
df_clean = df.dropna(subset=['year','rating','genres'])
df_clean_genre = df_clean.dropna(subset=['genres'])

In [ ]:
df_clean_genre.info()

<class 'pandas.core.frame.DataFrame'>
Index: 4685 entries, 135 to 23456
Data columns (total 10 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   name                4685 non-null   object        
 1   first_release_date  4685 non-null   datetime64[ns]
 2   genres              4685 non-null   object        
 3   platforms           4685 non-null   object        
 4   summary             4685 non-null   object        
 5   rating              4685 non-null   float64       
 6   rating_count        4685 non-null   float64       
 7   cover               4684 non-null   object        
 8   year                4685 non-null   int32         
 9   decennie            4685 non-null   int32         
dtypes: datetime64[ns](1), float64(2), int32(2), object(5)
memory usage: 366.0+ KB


In [ ]:
# Séparer les genres en une liste en utilisant plusieurs séparateurs
df_clean['genres_split'] = df_clean['genres'].str.split(r',\s*|\s*,\s*')

# Supprimer les espaces en trop autour des genres
df_clean['genres_split'] = df_clean['genres_split'].apply(lambda x: [genre.strip() for genre in x])

# Créer une liste unique de genres
all_genres = set(genre for sublist in df_clean['genres_split'] for genre in sublist)

# Créer des colonnes pour chaque genre
for genre in all_genres:
    df_clean[genre] = df_clean['genres_split'].apply(lambda x: 1 if genre in x else 0)

# Supprimer la colonne temporaire 'genres_split'
df_clean = df_clean.drop(columns=['genres_split'])


<ipython-input-41-e094f9c1c9bc>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean['genres_split'] = df_clean['genres'].str.split(r',\s*|\s*,\s*')
<ipython-input-41-e094f9c1c9bc>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean['genres_split'] = df_clean['genres_split'].apply(lambda x: [genre.strip() for genre in x])
<ipython-input-41-e094f9c1c9bc>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value i

In [ ]:
# Garder les lignes où au moins une des colonnes PlayStation 5, Xbox Series, ou Switch est égale à 1
df_clean_filtered = df_clean[(df_clean['PlayStation 5'] == 1) |
                             (df_clean['Xbox Series'] == 1) |
                             (df_clean['Nintendo Switch'] == 1)]
df_clean_filtered.head()

KeyError: 'Xbox Series'

In [ ]:
df_clean.info()

<class 'pandas.core.frame.DataFrame'>
Index: 4685 entries, 135 to 23456
Data columns (total 34 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   name                        4685 non-null   object        
 1   first_release_date          4685 non-null   datetime64[ns]
 2   genres                      4685 non-null   object        
 3   platforms                   4685 non-null   object        
 4   summary                     4685 non-null   object        
 5   rating                      4685 non-null   float64       
 6   rating_count                4685 non-null   float64       
 7   cover                       4684 non-null   object        
 8   year                        4685 non-null   int32         
 9   decennie                    4685 non-null   int32         
 10                              4685 non-null   int64         
 11  Tactical                    4685 non-null   int64         

In [ ]:
df_clean.head()

name first_release_date  \
135                   Shadows of Doubt         2024-09-26   
201                        Frostpunk 2         2024-09-20   
235                     Aura of Worlds         2024-09-19   
256                  The Plucky Squire         2024-09-17   
346  Warhammer 40,000: Space Marine II         2024-09-09   

                                                genres  \
135               Role-playing (RPG), Adventure, Indie   
201                         Simulator, Strategy, Indie   
235  Platform, Role-playing (RPG), Strategy, Tactic...   
256                        Platform, Puzzle, Adventure   
346             Shooter, Role-playing (RPG), Adventure   

                                             platforms  \
135  PC (Microsoft Windows), PlayStation 5, Xbox Se...   
201  PC (Microsoft Windows), Mac, PlayStation 5, Xb...   
235  Linux, PC (Microsoft Windows), Mac, Nintendo S...   
256  PC (Microsoft Windows), Nintendo Switch, PlayS...   
346  PC (Microsoft Windows), PlayStation 5, Xbox Se...   

                                               summary     rating  \
135  Shadows of Doubt is a detective stealth game s...  70.628078   
201  Frostpunk 2 is the sequel to the highly acclai...  81.094314   
235  "Aura of worlds is a creative tactics rogue-li...  70.000000   
256  Storybook characters discover a three-dimensio...  70.080896   
346  The galaxy is in peril. Entire worlds are fall...  79.727888   

     rating_count                                              cover  year  \
135           5.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
201           8.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
235           0.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
256           8.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
346          27.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   

     decennie     Tactical  MOBA  Adventure  Turn-based strategy (TBS)  \
135      2020  0         0     0          1                          0   
201      2020  0         0     0          0                          0   
235      2020  0         1     0          1                          0   
256      2020  0         0     0          1                          0   
346      2020  0         0     0          1                          0   

     Visual Novel  Hack and slash/Beat 'em up  Quiz/Trivia  Music  Pinball  \
135             0                           0            0      0        0   
201             0                           0            0      0        0   
235             0                           0            0      0        0   
256             0                           0            0      0        0   
346             0                           0            0      0        0   

     Sport  Point-and-click  Real Time Strategy (RTS)  Fighting  Indie  \
135      0                0                         0         0      1   
201      0                0                         0         0      1   
235      0                0                         0         0      1   
256      0                0                         0         0      0   
346      0                0                         0         0      0   

     Arcade  Racing  Shooter  Puzzle  Strategy  Card & Board Game  \
135       0       0        0       0         0                  0   
201       0       0        0       0         1                  0   
235       0       0        0       0         1                  0   
256       0       0        0       1         0                  0   
346       0       0        1       0         0                  0   

     Role-playing (RPG)  Platform  Simulator  
135                   1         0          0  
201                   0         0          1  
235                   1         1          0  
256                   0         1          0  
346                   1         0          0

In [ ]:
# Remplacer les valeurs nulles par une chaîne vide pour éviter les erreurs
df_clean['platforms'] = df_clean['platforms'].fillna('')

# Séparer les plateformes en une liste en utilisant plusieurs séparateurs
df_clean['platforms_split'] = df_clean['platforms'].str.split(r',\s*|\s*,\s*')

# Supprimer les espaces en trop autour des plateformes
df_clean['platforms_split'] = df_clean['platforms_split'].apply(lambda x: [platform.strip() for platform in x])

# Créer une liste unique de plateformes
all_platforms = set(platform for sublist in df_clean['platforms_split'] for platform in sublist)

# Créer des colonnes pour chaque plateforme
for platform in all_platforms:
    df_clean[platform] = df_clean['platforms_split'].apply(lambda x: 1 if platform in x else 0)

# Supprimer la colonne temporaire 'platforms_split'
df_clean = df_clean.drop(columns=['platforms_split'])


In [ ]:
df_clean.info()

<class 'pandas.core.frame.DataFrame'>
Index: 4685 entries, 135 to 23456
Data columns (total 95 columns):
 #   Column                                                                  Non-Null Count  Dtype         
---  ------                                                                  --------------  -----         
 0   name                                                                    4685 non-null   object        
 1   first_release_date                                                      4685 non-null   datetime64[ns]
 2   genres                                                                  4685 non-null   object        
 3   platforms                                                               4685 non-null   object        
 4   summary                                                                 4685 non-null   object        
 5   rating                                                                  4685 non-null   float64       
 6   rating_count              

In [ ]:
df_clean.head(5)

name first_release_date  \
135                   Shadows of Doubt         2024-09-26   
201                        Frostpunk 2         2024-09-20   
235                     Aura of Worlds         2024-09-19   
256                  The Plucky Squire         2024-09-17   
346  Warhammer 40,000: Space Marine II         2024-09-09   

                                                genres  \
135               Role-playing (RPG), Adventure, Indie   
201                         Simulator, Strategy, Indie   
235  Platform, Role-playing (RPG), Strategy, Tactic...   
256                        Platform, Puzzle, Adventure   
346             Shooter, Role-playing (RPG), Adventure   

                                             platforms  \
135  PC (Microsoft Windows), PlayStation 5, Xbox Se...   
201  PC (Microsoft Windows), Mac, PlayStation 5, Xb...   
235  Linux, PC (Microsoft Windows), Mac, Nintendo S...   
256  PC (Microsoft Windows), Nintendo Switch, PlayS...   
346  PC (Microsoft Windows), PlayStation 5, Xbox Se...   

                                               summary     rating  \
135  Shadows of Doubt is a detective stealth game s...  70.628078   
201  Frostpunk 2 is the sequel to the highly acclai...  81.094314   
235  "Aura of worlds is a creative tactics rogue-li...  70.000000   
256  Storybook characters discover a three-dimensio...  70.080896   
346  The galaxy is in peril. Entire worlds are fall...  79.727888   

     rating_count                                              cover  year  \
135           5.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
201           8.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
235           0.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
256           8.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
346          27.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   

     decennie     Tactical  MOBA  Adventure  Turn-based strategy (TBS)  \
135      2020  0         0     0          1                          0   
201      2020  0         0     0          0                          0   
235      2020  0         1     0          1                          0   
256      2020  0         0     0          1                          0   
346      2020  0         0     0          1                          0   

     Visual Novel  Hack and slash/Beat 'em up  Quiz/Trivia  Music  Pinball  \
135             0                           0            0      0        0   
201             0                           0            0      0        0   
235             0                           0            0      0        0   
256             0                           0            0      0        0   
346             0                           0            0      0        0   

     Sport  Point-and-click  Real Time Strategy (RTS)  Fighting  Indie  \
135      0                0                         0         0      1   
201      0                0                         0         0      1   
235      0                0                         0         0      1   
256      0                0                         0         0      0   
346      0                0                         0         0      0   

     Arcade  Racing  Shooter  Puzzle  Strategy  Card & Board Game  \
135       0       0        0       0         0                  0   
201       0       0        0       0         1                  0   
235       0       0        0       0         1                  0   
256       0       0        0       1         0                  0   
346       0       0        1       0         0                  0   

     Role-playing (RPG)  Platform  Simulator  \
135                   1         0          0   
201                   0         0          1   
235                   1         1          0   
256                   0         1          0   
346                   1         0          0   

     PC (Microsoft Win

In [ ]:
df_clean = df_clean.reset_index(drop=True)
df_clean

name first_release_date  \
0                      Shadows of Doubt         2024-09-26   
1                           Frostpunk 2         2024-09-20   
2                        Aura of Worlds         2024-09-19   
3                     The Plucky Squire         2024-09-17   
4     Warhammer 40,000: Space Marine II         2024-09-09   
...                                 ...                ...   
4680                   Strikers 1945 II         1997-12-31   
4681     Putt-Putt Travels Through Time         1997-11-21   
4682            Spy Fox in "Dry Cereal"         1997-10-17   
4683                    Chasm: The Rift         1997-09-30   
4684            Oddworld: Abe's Oddysee         1997-09-18   

                                                 genres  \
0                  Role-playing (RPG), Adventure, Indie   
1                            Simulator, Strategy, Indie   
2     Platform, Role-playing (RPG), Strategy, Tactic...   
3                           Platform, Puzzle, Adventure   
4                Shooter, Role-playing (RPG), Adventure   
...                                                 ...   
4680                                    Shooter, Arcade   
4681                         Point-and-click, Adventure   
4682                         Point-and-click, Adventure   
4683                                  Fighting, Shooter   
4684                        Platform, Puzzle, Adventure   

                                              platforms  \
0     PC (Microsoft Windows), PlayStation 5, Xbox Se...   
1     PC (Microsoft Windows), Mac, PlayStation 5, Xb...   
2     Linux, PC (Microsoft Windows), Mac, Nintendo S...   
3     PC (Microsoft Windows), Nintendo Switch, PlayS...   
4     PC (Microsoft Windows), PlayStation 5, Xbox Se...   
...                                                 ...   
4680  PC (Microsoft Windows), PlayStation, Sega Satu...   
4681  PC (Microsoft Windows), Mac, Android, iOS, Pla...   
4682  Wii, PC (Microsoft Windows), Mac, iOS, PlaySta...   
4683  PC (Microsoft Windows), DOS, PlayStation 4, Xb...   
4684  PC (Microsoft Windows), PlayStation, PlayStati...   

                                                summary     rating  \
0     Shadows of Doubt is a detective stealth game s...  70.628078   
1     Frostpunk 2 is the sequel to the highly acclai...  81.094314   
2     "Aura of worlds is a creative tactics rogue-li...  70.000000   
3     Storybook characters discover a three-dimensio...  70.080896   
4     The galaxy is in peril. Entire worlds are fall...  79.727888   
...                                                 ...        ...   
4680  Continuing where the last game ended, the forc...  83.000000   
4681  Mr. Firebird's time machine has gone haywire a...  82.038293   
4682  The super-suave agent, SPY Fox, must find Mr. ...  79.942740   
4683  Humankind, in the process of evolution, has en...  50.082482   
4684  Oddworld: Abe's Oddysee is the first game set ...  82.397021   

      rating_count                                              cover  year  \
0              5.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
1              8.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
2              0.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
3              8.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
4             27.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  2024   
...            ...                                                ...   ...   
4680           4.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  1997   
4681           9.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  1997   
4682          11.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  1997   
4683           6.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  1997   
4684         218.0  //images.igdb.com/igdb/image/upload/t_thumb/co...  1997   

      decennie     Tactical  MOBA  Adventure  Turn-based strategy (TBS)  \
0      

In [ ]:
df_export = df_clean


In [ ]:
df_export.to_parquet('df_igdb.parquet', index=False)
files.download('df_igdb.parquet')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
pip install ydata_profiling

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 356.2/356.2 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 17.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 686.1/686.1 kB 27.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.8/104.8 kB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 59.1 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27081 sha256=3b9bdca65dbeaf45541cf0ae09f4c2465a19cd38c3404ab51bc5d1aca2cee10c
  Stored in directory: /root/.cache/pip/wheels/dd/91/29/a79cecb328d01739e64017b6fb9a1ab9d8cb1853098ec5966d
Successfully built htmlmin


In [ ]:

# import pour ydata_profiling
import ydata_profiling
from ydata_profiling import ProfileReport
from ydata_profiling.utils.cache import cache_file

# creation d'un rapport exploratoire de notre dataframe

profile = ProfileReport(df_clean, title="Analyse Générale",html={'style': {'full_width': True}})

# Affichage de notre rapport exploratoire :

profile.to_notebook_iframe()


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
df_clean.shape

(4685, 95)

In [ ]:
#px.line(df_total2, x="released", y=df_total2.select_dtypes(include='number').columns, title="Titre")